<a href="https://colab.research.google.com/github/yaswhar/learning-genesis-sim/blob/main/Cloth%20Simulation.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install genesis-world -q
!pip install mediapy -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 107.3/107.3 kB 3.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 41.4/41.4 kB 3.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.4/44.4 kB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 109.7/109.7 kB 7.4 MB/s eta 0:00:00
  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.3/81.3 kB 2.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 82.7/82.7 MB 11.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.4/6.4 MB 96.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 409.3/409.3 kB 32.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 55.0/55.0 MB 17.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.1/2.1 MB 63.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━

In [ ]:
import os
NVIDIA_ICD_CONFIG_PATH = '/usr/share/glvnd/egl_vendor.d/10_nvidia.json'
ICD_CONFIG_CONTENT = """{
    "file_format_version" : "1.0.0",
    "ICD" : {
        "library_path" : "libEGL_nvidia.so.0"
    }
}
"""
with open(NVIDIA_ICD_CONFIG_PATH, 'w') as f:
    f.write(ICD_CONFIG_CONTENT)

In [ ]:
import genesis as gs
import numpy as np
import torch
import mediapy as media
from tqdm.notebook import tqdm

gs.init(backend=gs.cuda)

[Genesis] [20:40:03] [INFO] ╭───────────────────────────────────────────────╮
INFO:genesis:~<╭───────────────────────────────────────────────╮>~
[Genesis] [20:40:03] [INFO] │┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈ Genesis ┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈│
INFO:genesis:~<│┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈>~ ~~~~<Genesis>~~~~ ~<┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈┉┈│>~
[Genesis] [20:40:03] [INFO] ╰───────────────────────────────────────────────╯
INFO:genesis:~<╰───────────────────────────────────────────────╯>~
[Genesis] [20:40:03] [INFO] Running on [Tesla T4] with backend gs.cuda. Device memory: 14.74 GB.
INFO:genesis:Running on ~~<[Tesla T4]>~~ with backend ~~<gs.cuda>~~. Device memory: ~~<14.74>~~ GB.
[Genesis] [20:40:04] [INFO] 🚀 Genesis initialized. 🔖 version: 0.2.1, 🌱 seed: None, 📏 precision: '32', 🐛 debug: False, 🎨 theme: 'dark'.
INFO:genesis:🚀 Genesis initialized. 🔖 version: ~~<0.2.1>~~, 🌱 seed: ~~<None>~~, 📏 precision: '~~<32>~~', 🐛 debug: ~~<False>~~, 🎨 theme: '~~<dark>~~'.


In [ ]:
# Create Scene
scene = gs.Scene(
    sim_options=gs.options.SimOptions(
        dt       = 4e-3,
        substeps = 10,
    ),
    viewer_options=gs.options.ViewerOptions(
        camera_fov = 30,
        res        = (1280, 720),
        max_FPS    = 60,
    ),
    show_viewer = False,
)
cam = scene.add_camera(
    res    = (640, 480),
    pos    = (3.5, 0.0, 2.5),
    lookat = (0, 0, 0.5),
    fov    = 30,
    GUI    = False,
)

[Genesis] [20:40:08] [INFO] Scene <f995b24> created.
INFO:genesis:Scene ~~~<<f995b24>>~~~ created.


In [ ]:
# Add Entities
plane = scene.add_entity(
    morph=gs.morphs.Plane(),
)

cloth_1 = scene.add_entity(
    material=gs.materials.PBD.Cloth(),
    morph=gs.morphs.Mesh(
        file='meshes/cloth.obj',
        scale=2.0,
        pos=(0, 0, 0.5),
        euler=(0.0, 0, 0.0),
    ),
    surface=gs.surfaces.Default(
        color=(0.2, 0.4, 0.8, 1.0),
        vis_mode='visual',
    )
)

cloth_2 = scene.add_entity(
    material=gs.materials.PBD.Cloth(),
    morph=gs.morphs.Mesh(
        file='meshes/cloth.obj',
        scale=2.0,
        pos=(0, 0, 1.0),
        euler=(0.0, 0, 0.0),
    ),
    surface=gs.surfaces.Default(
        color=(0.8, 0.4, 0.2, 1.0),
        vis_mode='particle',
    )
)

[Genesis] [20:40:14] [INFO] Adding <gs.RigidEntity>. idx: 0, uid: <578f194>, morph: <gs.morphs.Plane>, material: <gs.materials.Rigid>.
INFO:genesis:Adding ~<<gs.RigidEntity>>~. idx: ~<0>~, uid: ~~~<<578f194>>~~~, morph: ~<<gs.morphs.Plane>>~, material: ~<<gs.materials.Rigid>>~.
[Genesis] [20:40:15] [INFO] Preprocessing geom idx 0.
INFO:genesis:Preprocessing geom idx ~~<0>~~.
[Genesis] [20:40:15] [INFO] Adding <gs.PBD2DEntity>. idx: 1, uid: <5d91f9b>, morph: <gs.morphs.Mesh(file='/usr/local/lib/python3.11/dist-packages/genesis/assets/meshes/cloth.obj')>, material: <gs.PBD.Cloth>.
INFO:genesis:Adding ~<<gs.PBD2DEntity>>~. idx: ~<1>~, uid: ~~~<<5d91f9b>>~~~, morph: ~<<gs.morphs.Mesh(file='/usr/local/lib/python3.11/dist-packages/genesis/assets/meshes/cloth.obj')>>~, material: ~<<gs.PBD.Cloth>>~.
[Genesis] [20:40:15] [INFO] Remeshing for tetrahedralization...
INFO:genesis:Remeshing for tetrahedralization...
[Genesis] [20:40:17] [INFO] Adding <gs.PBD2DEntity>. idx: 2, uid: <8ec865a>, morph: 

In [ ]:
# Build
scene.build()

[Genesis] [20:40:22] [INFO] Building scene <f995b24>...
INFO:genesis:Building scene ~~~<<f995b24>>~~~...
[Genesis] [20:40:38] [INFO] Compiling simulation kernels...
INFO:genesis:Compiling simulation kernels...
[Genesis] [20:41:40] [INFO] Building visualizer...
INFO:genesis:Building visualizer...


In [ ]:
# Fixing the ends
cloth_1.fix_particle(cloth_1.find_closest_particle((-1, -1, 1.0)))
cloth_1.fix_particle(cloth_1.find_closest_particle((1, 1, 1.0)))
cloth_1.fix_particle(cloth_1.find_closest_particle((-1, 1, 1.0)))
cloth_1.fix_particle(cloth_1.find_closest_particle((1, -1, 1.0)))

cloth_2.fix_particle(cloth_2.find_closest_particle((-1, -1, 1.0)))

In [ ]:
# Run
horizon = 1000
frames = []
for i in range(horizon):
    scene.step()
    frames.append(cam.render()[0])

[Genesis] [20:42:38] [INFO] Running at 0.82 FPS.
INFO:genesis:Running at ~<0.82>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 0.85 FPS.
INFO:genesis:Running at ~<0.85>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 0.89 FPS.
INFO:genesis:Running at ~<0.89>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 0.93 FPS.
INFO:genesis:Running at ~<0.93>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 0.98 FPS.
INFO:genesis:Running at ~<0.98>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 1.03 FPS.
INFO:genesis:Running at ~<1.03>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 1.08 FPS.
INFO:genesis:Running at ~<1.08>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 1.13 FPS.
INFO:genesis:Running at ~<1.13>~ FPS.
[Genesis] [20:42:38] [INFO] Running at 1.19 FPS.
INFO:genesis:Running at ~<1.19>~ FPS.
[Genesis] [20:42:39] [INFO] Running at 1.25 FPS.
INFO:genesis:Running at ~<1.25>~ FPS.
[Genesis] [20:42:39] [INFO] Running at 1.31 FPS.
INFO:genesis:Running at ~<1.31>~ FPS.
[Genesis] [20:42:39] [INFO] Running at 1.37

In [ ]:
media.show_video(frames, fps=200)

This browser does not support the video tag.
